In [2]:
import pickle
import json
import networkx as nx
import pandas as pd
import numpy as np
import igraph as ig
from igraph import Graph, VertexClustering
from collections import defaultdict, Counter
import random

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


In [3]:
with open('components/ind_to_name.json', 'r') as f:
    ind_to_name = json.load(f)
with open('components/name_to_ind.json', 'r') as f:
    name_to_ind = json.load(f)

In [4]:
df = pd.read_csv('components/nodes.csv').drop('Unnamed: 0', axis=1)

In [5]:
def get_genres(df, i):
    row = df.loc[i].to_dict()
    row = {k:v for (k, v) in row.items() if v != 0}
    row.pop("id")
    row.pop("popularity")
    row.pop("name")
    row.pop("followers")
    return list(row.keys())

In [6]:
print(df.columns)

Index(['id', 'name', 'followers', 'popularity', 'australian psych',
       'rap marseille', 'political hip hop', 'uk melodic rap',
       'samba paulista', 'desi trap',
       ...
       'nigerian hip hop', 'supergroup', 'early music', 'forro de favela',
       'rap siciliano', 'russian electronic', 'afropop', 'deep pop edm',
       'dark disco', 'cuban rumba'],
      dtype='object', length=1347)


In [7]:
net_G = nx.read_graphml('components/graph.graphml')

In [8]:
G = Graph.from_networkx(net_G)

### connected components

In [9]:
cc = G.connected_components()
cc.sizes()

[2894]

### leiden

In [10]:
leiden_clustering = G.community_leiden(objective_function='modularity', resolution=1.4)

In [11]:
leiden_clustering.summary()

'Clustering with 2894 elements and 18 clusters'

In [12]:
# colors = ['#' + ''.join([random.choice('0123456789ABCDEF') for _ in range(6)]) + '80' for _ in range(len(leiden_clustering))]
# vertex_colors = [colors[community] for community in leiden_clustering.membership]

In [25]:
clusters = leiden_clustering.membership

In [49]:
unique_clusters = list(set(clusters))
cluster_colors = {cluster: '#' + ''.join([random.choice('0123456789ABCDEF') for _ in range(6)]) for cluster in unique_clusters}

vertex_colors = [cluster_colors[cluster] + "60" for cluster in clusters]

edge_colors = []
for edge in G.es:
    source_cluster = clusters[edge.source]
    target_cluster = clusters[edge.target]
    
    if source_cluster == target_cluster:
        edge_colors.append(cluster_colors[source_cluster] + "30") 
    else:
        edge_colors.append('#00000000')

In [13]:
leiden_clustering.sizes()

[262, 311, 281, 4, 355, 247, 568, 141, 166, 61, 59, 204, 79, 70, 76, 5, 3, 2]

In [14]:
members = leiden_clustering.membership
members_map = defaultdict(list)
for i in range(len(members)):
    members_map[members[i]].append(i)
print(members_map)

defaultdict(<class 'list'>, {0: [0, 10, 19, 20, 25, 30, 31, 36, 37, 38, 41, 43, 47, 55, 60, 68, 69, 73, 86, 93, 97, 106, 113, 120, 123, 126, 135, 142, 144, 154, 161, 166, 168, 169, 170, 172, 177, 180, 199, 202, 203, 205, 218, 225, 227, 228, 235, 241, 243, 257, 268, 301, 318, 325, 341, 342, 350, 351, 353, 357, 358, 365, 366, 368, 369, 377, 380, 382, 387, 394, 401, 412, 414, 423, 426, 443, 447, 453, 462, 476, 482, 483, 484, 496, 498, 499, 510, 516, 529, 543, 565, 566, 615, 636, 658, 662, 668, 708, 712, 717, 719, 731, 748, 752, 762, 767, 777, 789, 792, 793, 809, 810, 812, 814, 839, 841, 846, 864, 872, 886, 905, 916, 930, 931, 943, 953, 955, 963, 967, 969, 974, 979, 983, 995, 1045, 1050, 1066, 1074, 1085, 1086, 1098, 1106, 1107, 1110, 1122, 1141, 1146, 1154, 1190, 1199, 1205, 1209, 1210, 1212, 1224, 1230, 1255, 1257, 1294, 1313, 1315, 1341, 1349, 1350, 1392, 1399, 1404, 1421, 1429, 1470, 1477, 1478, 1487, 1494, 1499, 1529, 1552, 1560, 1574, 1624, 1627, 1628, 1630, 1667, 1672, 1680, 1683, 1

In [15]:
for _, v in members_map.items():
    names = []
    genres = []
    for a in v:
        names.append(ind_to_name[str(a)])
        genres = genres + get_genres(df, a)
    print(names)
    print(Counter(genres).most_common(3))

['Bad Bunny', 'Rauw Alejandro', 'J Balvin', 'Feid', 'Daddy Yankee', 'KAROL G', 'Bizarrap', 'Ozuna', 'Anuel AA', 'ROSALÍA', 'Quevedo', 'Shakira', 'Myke Towers', 'Maluma', 'Jhay Cortez', 'Farruko', 'Manuel Turizo', 'Duki', 'Sech', 'Maria Becerra', 'Mora', 'Romeo Santos', 'Nicky Jam', 'Sebastian Yatra', 'Camilo', 'De La Ghetto', 'Rels B', 'Arcangel', 'Black Eyed Peas', 'Becky G', 'Tiago PZK', 'Eladio Carrion', 'Justin Quiles', 'Ñengo Flow', 'Don Omar', 'Lenny Tavárez', 'Wisin & Yandel', 'Jay Wheeler', 'TINI', 'Paulo Londra', 'Tainy', 'Zion & Lennox', 'Nicki Nicole', 'Cris Mj', 'El Alfa', 'Reik', 'Pailita', 'Danny Ocean', 'Plan B', 'Polimá Westcoast', 'Aventura', 'Wisin', 'Dalex', 'Ryan Castro', 'Prince Royce', 'Brray', 'Natanael Cano', 'Lyanno', 'Enrique Iglesias', 'Natti Natasha', 'Bryant Myers', 'Jonas Brothers', 'Standly', 'KHEA', 'Noriel', 'Mambo Kingz', 'Tony Dize', 'Jennifer Lopez', 'Trueno', 'Luis Fonsi', 'Yandel', 'Luar La L', 'Darell', 'Piso 21', 'C. Tangana', 'DJ Luian', 'Brytia

### degree

In [77]:
degrees = G.degree()

In [78]:
mapped_degrees = {ind_to_name[str(i)]:degrees[i] for i in range(len(degrees))}
mapped_degrees = dict(sorted(mapped_degrees.items(), key=lambda item: -item[1]))
mapped_degrees

{'Ty Dolla $ign': 170,
 'R3HAB': 166,
 'Snoop Dogg': 161,
 'French Montana': 152,
 'Gucci Mane': 148,
 'Lil Wayne': 147,
 'David Guetta': 139,
 'J Balvin': 138,
 'Chris Brown': 133,
 'Future': 132,
 'Steve Aoki': 131,
 'Diplo': 129,
 'Wiz Khalifa': 128,
 'Farruko': 127,
 '2 Chainz': 126,
 'Nicki Minaj': 121,
 'Tiësto': 117,
 'Tyga': 117,
 'Young Thug': 116,
 'Rick Ross': 115,
 'De La Ghetto': 114,
 'Juicy J': 110,
 'DJ Khaled': 109,
 'Nicky Jam': 109,
 'The Game': 108,
 'Pitbull': 106,
 'T.I.': 103,
 'Myke Towers': 99,
 'Busta Rhymes': 99,
 'Wale': 96,
 'Rauw Alejandro': 95,
 'Ozuna': 95,
 'Big Sean': 94,
 'Bad Bunny': 92,
 'Yandel': 92,
 'Major Lazer': 91,
 'Lil Baby': 90,
 'Arcangel': 90,
 'Lil Durk': 88,
 'Anitta': 88,
 'Kanye West': 87,
 'Sean Paul': 87,
 'Tory Lanez': 87,
 'Wisin': 87,
 'Drake': 85,
 'Maluma': 85,
 'Quavo': 85,
 'Meek Mill': 85,
 'Ed Sheeran': 84,
 'Calvin Harris': 84,
 'Rich The Kid': 84,
 'YG': 83,
 'Yo Gotti': 83,
 'Justin Bieber': 81,
 'Daddy Yankee': 81,
 'A 

### harmonic centrality

In [80]:
harm_centralities = G.harmonic_centrality()

In [88]:
mapped_harm_centralities = {ind_to_name[str(i)]:harm_centralities[i] for i in range(len(harm_centralities))}
mapped_harm_centralities = dict(sorted(mapped_harm_centralities.items(), key=lambda item: -item[1]))
for i in range(len(mapped_harm_centralities.keys())):
    k = list(mapped_harm_centralities.keys())[i]
    print(i, k, round(mapped_harm_centralities[k], 2))

0 R3HAB 0.43
1 Snoop Dogg 0.42
2 J Balvin 0.42
3 French Montana 0.42
4 Ty Dolla $ign 0.42
5 Diplo 0.42
6 Steve Aoki 0.42
7 David Guetta 0.42
8 Tiësto 0.41
9 Lil Wayne 0.41
10 Tyga 0.41
11 Gucci Mane 0.41
12 Farruko 0.41
13 Major Lazer 0.4
14 Chris Brown 0.4
15 Sean Paul 0.4
16 Pitbull 0.4
17 Nicki Minaj 0.4
18 Wiz Khalifa 0.4
19 Future 0.4
20 2 Chainz 0.4
21 Anitta 0.4
22 Rick Ross 0.4
23 Ed Sheeran 0.4
24 Juicy J 0.39
25 Busta Rhymes 0.39
26 Wale 0.39
27 Justin Bieber 0.39
28 Nicky Jam 0.39
29 Young Thug 0.39
30 Maluma 0.39
31 DJ Khaled 0.39
32 Becky G 0.39
33 The Game 0.39
34 Khalid 0.39
35 G-Eazy 0.39
36 Tory Lanez 0.39
37 Akon 0.39
38 Afrojack 0.39
39 Calvin Harris 0.39
40 Ozuna 0.39
41 De La Ghetto 0.39
42 John Legend 0.39
43 Dimitri Vegas & Like Mike 0.39
44 will.i.am 0.39
45 Quavo 0.38
46 Daddy Yankee 0.38
47 DJ Snake 0.38
48 Lil Baby 0.38
49 A Boogie Wit da Hoodie 0.38
50 T.I. 0.38
51 Pharrell Williams 0.38
52 Yandel 0.38
53 Alok 0.38
54 T-Pain 0.38
55 Dua Lipa 0.38
56 Dillon F

### eigenvector centrality

In [66]:
eig_centralities = G.eigenvector_centrality(directed=False)

In [87]:
mapped_eig_centralities = {ind_to_name[str(i)]:eig_centralities[i] for i in range(len(eig_centralities))}
mapped_eig_centralities = dict(sorted(mapped_eig_centralities.items(), key=lambda item: -item[1]))
for i in range(len(mapped_eig_centralities.keys())):
    k = list(mapped_eig_centralities.keys())[i]
    print(i, k, round(mapped_eig_centralities[k], 2))

0 Ty Dolla $ign 1.0
1 French Montana 0.99
2 Lil Wayne 0.95
3 Future 0.92
4 Chris Brown 0.92
5 Gucci Mane 0.92
6 2 Chainz 0.89
7 DJ Khaled 0.82
8 Snoop Dogg 0.82
9 Tyga 0.81
10 Rick Ross 0.8
11 Nicki Minaj 0.8
12 Young Thug 0.79
13 Wiz Khalifa 0.78
14 The Game 0.74
15 J Balvin 0.72
16 Meek Mill 0.71
17 Juicy J 0.71
18 T.I. 0.7
19 Big Sean 0.68
20 Jeezy 0.64
21 Yo Gotti 0.63
22 Quavo 0.62
23 YG 0.61
24 Wale 0.61
25 Farruko 0.6
26 Drake 0.59
27 Busta Rhymes 0.59
28 Kanye West 0.58
29 Lil Durk 0.58
30 Tory Lanez 0.56
31 Travis Scott 0.55
32 Lil Baby 0.54
33 Nicky Jam 0.53
34 Rich The Kid 0.53
35 De La Ghetto 0.53
36 Ludacris 0.52
37 Trey Songz 0.52
38 21 Savage 0.52
39 Jeremih 0.52
40 David Guetta 0.51
41 Myke Towers 0.51
42 Rauw Alejandro 0.51
43 Gunna 0.5
44 Nas 0.49
45 Ozuna 0.49
46 T-Pain 0.49
47 Pharrell Williams 0.49
48 Yandel 0.48
49 Bad Bunny 0.48
50 Pusha T 0.48
51 Fabolous 0.48
52 Mike WiLL Made-It 0.47
53 A Boogie Wit da Hoodie 0.47
54 Migos 0.47
55 G-Eazy 0.47
56 Arcangel 0.46


### clustering

In [16]:
for clique in G.largest_cliques():
    artists = set()
    for a in clique:
        artists.add(ind_to_name[str(a)])
        row = df.loc[a].to_dict()
        row = { (k, v) for (k, v) in row.items() if type(v) != str and v > 0 and k not in ['followers', 'popularity']}
        print(row)
    print(artists)

{('modern bollywood', 1), ('sufi', 1), ('desi pop', 1), ('filmi', 1), ('classic pakistani pop', 1)}
{('desi pop', 1), ('filmi', 1), ('modern bollywood', 1)}
{('desi pop', 1), ('modern bollywood', 1)}
{('desi pop', 1), ('filmi', 1), ('modern bollywood', 1), ('desi hip hop', 1)}
{('desi pop', 1), ('filmi', 1), ('modern bollywood', 1)}
{('modern bollywood', 1), ('classic bollywood', 1), ('desi hip hop', 1), ('desi pop', 1), ('filmi', 1)}
{('desi pop', 1), ('filmi', 1), ('modern bollywood', 1)}
{('desi pop', 1), ('filmi', 1), ('modern bollywood', 1)}
{('desi pop', 1), ('filmi', 1), ('modern bollywood', 1), ('desi hip hop', 1)}
{('desi pop', 1), ('filmi', 1), ('modern bollywood', 1)}
{('filmi', 1), ('tollywood', 1)}
{('desi pop', 1), ('filmi', 1), ('modern bollywood', 1)}
{('desi pop', 1), ('filmi', 1), ('modern bollywood', 1)}
{('desi pop', 1), ('filmi', 1), ('modern bollywood', 1)}
{('modern bollywood', 1), ('desi hip hop', 1), ('haryanvi pop', 1), ('desi pop', 1), ('desi trap', 1)}
{('de

In [58]:
# layout = G.layout_drl(options={"edge.cut": 0.5})
layout = G.layout_drl(options={"edge.cut": 1, "init_attraction": 1e6, "liquid_attraction": 1e6, "expansion_attraction": 1e6, "cooldown_attraction": 1e6})
visual_style = {
    "vertex_size": 10,
    "vertex_frame_color": None,
    "vertex_color": vertex_colors,
    "vertex_border": 0,
    "edge_width": 10,
    "edge_color": edge_colors,
    "layout": layout,
    "bbox": (2500, 2000),
    "autocurve": True,
    "background": "#0E0E10"
}
ig.plot(G, **visual_style)

### edge betweenness centrality

In [110]:
edge_betweenness = G.edge_betweenness(directed=False)
edges = G.get_edgelist()
edges_and_betweenness = zip(edges, edge_betweenness)
edges_and_betweenness = sorted(edges_and_betweenness, key=lambda x:-x[1])
i = 1
for edge, betweenness in edges_and_betweenness:
    u, v = edge
    uname, vname = ind_to_name[str(u)], ind_to_name[str(v)]
    print(f'{i}. {uname}, {vname}')
    if i >= 25: break
    i += 1

1. Pritam, Diplo
2. Trippie Redd, Scarlxrd
3. Kordhell, Scarlxrd
4. Kordhell, Dxrk ダーク
5. A.R. Rahman, Wale
6. Sfera Ebbasta, Quebonafide
7. Ozuna, Summer Cem
8. R3HAB, Sachin-Jigar
9. J Balvin, Badshah
10. Machine Gun Kelly, CORPSE
11. Summer Cem, Anıl Piyancı
12. Dxrk ダーク, Ghostface Playa
13. Kordhell, CORPSE
14. R3HAB, Nikhita Gandhi
15. Steve Aoki, Shaan
16. Miel San Marcos, for KING & COUNTRY
17. Enrique Iglesias, Sunidhi Chauhan
18. Snoop Dogg, Johnny Cash
19. Snoop Dogg, Leo Santana
20. Tiësto, Badshah
21. R3HAB, for KING & COUNTRY
22. Pitbull, Guru Randhawa
23. Pritam, Marshmello
24. Maluma, Grupo Firme
25. Diplo, Bausa
